In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.optim import Adam

import lightning as L
from torch.utils.data import DataLoader, TensorDataset

OSError: [WinError 126] The specified module could not be found. Error loading "C:\Users\Edinam Tettey\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\torch\lib\fbgemm.dll" or one of its dependencies.

In [ ]:
# Adapted from StatQUest

class LSTMbyHand(L.LightningModule):
    def __init__(self):
        super().__init__()
        
        # use normal distribution to generate random weights and biases
        mean = torch.tensor(0.0)
        std = torch.tensor(1.0)

        # short term memory weights and biases
        self.wlr1 = nn.Parameter(torch.normal(mean=mean, std=std), requires_grad=True)
        self.wlr2 = nn.Parameter(torch.normal(mean=mean, std=std), requires_grad=True)
        self.blr1 = nn.Parameter(torch.tensor(0.), requires_grad=True)

        # candidate long term memory/cell state weights and biases
        self.wpr1 = nn.Parameter(torch.normal(mean=mean, std=std), requires_grad=True)
        self.wpr2 = nn.Parameter(torch.normal(mean=mean, std=std), requires_grad=True)
        self.bpr1 = nn.Parameter(torch.tensor(0.), requires_grad=True)

        # potential memory weights and biases
        self.wp1 = nn.Parameter(torch.normal(mean=mean, std=std), requires_grad=True)
        self.wp2 = nn.Parameter(torch.normal(mean=mean, std=std), requires_grad=True)
        self.bp1 = nn.Parameter(torch.tensor(0.), requires_grad=True)

        # output weights and biases
        self.wo1 = nn.Parameter(torch.normal(mean=mean, std=std), requires_grad=True)
        self.wo2 = nn.Parameter(torch.normal(mean=mean, std=std), requires_grad=True)
        self.bo1 = nn.Parameter(torch.tensor(0.), requires_grad=True)

    def input_format(self, wsh, win, b):
        data = {
            "input_weights": int(win.item()*1000),
            "gate_biases":int(b.item()*1000000),
            "short_weights":int(wsh.item()*1000)
        }
        return data
    
    def lstm_unit(self, input_value, long_memory, short_memory):
        # determine how much of long term memory to remember - forget gate
        long_remember_percent = torch.sigmoid((short_memory * self.wlr1)
                                              + (input_value * self.wlr2) +
                                              self.blr1)
        print(f"forget = {(short_memory * self.wlr1)+ (input_value * self.wlr2) +self.blr1}")
        # calculate how much of potential memory should be remembered - Candidate gate
        potential_remember_percent = torch.sigmoid((short_memory * self.wpr1)
                                              + (input_value * self.wpr2) +
                                              self.bpr1)
        print(f"candidate = {(short_memory * self.wpr1)  + (input_value * self.wpr2) + self.bpr1}")
        # calculate candidate memory - Input gate
        potential_memory = torch.tanh((short_memory * self.wp1)
                                              + (input_value * self.wp2) +
                                              self.bp1)
        print(f"input = {(short_memory * self.wp1)+ (input_value * self.wp2) +self.bp1}")
        # update long term memory
        updated_long_memory = ((long_memory * long_remember_percent) +
                               (potential_remember_percent * potential_memory))
        print(f"new_long = {updated_long_memory}")
        # calculate new short term memory and how much of it to output - Output gate
        output_percent = torch.sigmoid((short_memory * self.wo1) + 
                                       (input_value * self.wo2) +
                                       self.bo1)
        print(f"output = {(short_memory * self.wo1) + (input_value * self.wo2) +self.bo1}")
        updated_short_memory = torch.tanh(updated_long_memory) * output_percent
        print(f"new short = {updated_short_memory}")
        print(f"\n")

        return ([updated_long_memory, updated_short_memory])
    
    def forward(self, input):
        long_memory = 0
        short_memory = 0
        # test inputs
        day1 = input[0]
        day2 = input[1]
        day3 = input[2]
        day4 = input[3]

        long_memory, short_memory = self.lstm_unit(day1, long_memory, short_memory)
        long_memory, short_memory = self.lstm_unit(day2, long_memory, short_memory)
        long_memory, short_memory = self.lstm_unit(day3, long_memory, short_memory)
        long_memory, short_memory = self.lstm_unit(day4, long_memory, short_memory)

        return short_memory

    def configure_optimizers(self):
        return Adam(self.parameters())

    def training_step(self, batch, batch_idx):
        input_i, label_i = batch
        output_i = self.forward(input_i[0])
        loss = (output_i - label_i)**2

        self.log("train_loss ", loss)
        
        if (label_i == 0):
            self.log("Out 0", output_i)
        else:
            self.log("Out 1", output_i)
        return loss


In [ ]:

model = LSTMbyHand()
print("Company A: observed = 0, Predicted = ", model(torch.tensor([0., 0.25, 0.5, 1.])).detach())

forget = 0.0
candidate = 0.0
input = 0.0
new_long = 0.0
output = 0.0
new short = 0.0


forget = 0.0637499988079071
candidate = -0.11861167848110199
input = 0.015130866318941116
new_long = 0.007116740569472313
output = -0.23744790256023407
new short = 0.0031378273852169514


forget = 0.12774568796157837
candidate = -0.23928537964820862
input = 0.03303096070885658
new_long = 0.01832895539700985
output = -0.477364182472229
new short = 0.007016908377408981


forget = 0.25554943084716797
candidate = -0.4790578782558441
input = 0.06671610474586487
new_long = 0.03580855950713158
output = -0.9553114175796509
new short = 0.009944009594619274


Company A: observed = 0, Predicted =  tensor(0.0099)


In [ ]:
model = LSTMbyHand()
print("Company B: observed = 0.5, Predicted = ", model(torch.tensor([1., 0.25, 0.5, 1.])).detach())

forget = 0.41585028171539307
candidate = -1.6920146942138672
input = 0.6158304214477539
new_long = 0.08525400608778
output = 0.8518011569976807
new short = 0.059613995254039764


forget = 0.07857830077409744
candidate = -0.42610132694244385
input = 0.12275268882513046
new_long = 0.09255319833755493
output = 0.18987207114696503
new short = 0.05051261559128761


forget = 0.18641632795333862
candidate = -0.8486320972442627
input = 0.28147441148757935
new_long = 0.13278141617774963
output = 0.40634575486183167
new short = 0.07923182100057602


forget = 0.3821125328540802
candidate = -1.696131706237793
input = 0.5743565559387207
new_long = 0.15928348898887634
output = 0.8211283683776855
new short = 0.10969242453575134


Company B: observed = 0.5, Predicted =  tensor(0.1097)


In [ ]:
inputs = torch.tensor([[0., 0.25, 0.5, 1.], [1., 0.5, 0.25, 1.]])
labels = torch.tensor([0., 0.5])

In [ ]:
dataset = TensorDataset(inputs, labels)
dataloader = DataLoader(dataset)

In [ ]:
trainer = L.Trainer(max_epochs=3000)
trainer.fit(model, train_dataloaders=dataloader)

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
c:\Users\alosius.akonteh\AppData\Local\Programs\Python\Python312\Lib\site-packages\lightning\pytorch\trainer\connectors\logger_connector\logger_connector.py:75: Starting from v1.9.0, `tensorboardX` has been removed as a dependency of the `lightning.pytorch` package, due to potential conflicts with other packages in the ML ecosystem. For this reason, `logger=True` will use `CSVLogger` as the default logger, unless the `tensorboard` or `tensorboardX` packages are found. Please `pip install lightning[extra]` or one of them to enable TensorBoard support by default

  | Name         | Type | Params | Mode
---------------------------------------------
  | other params | n/a  | 12     | n/a 
---------------------------------------------
12        Trainable params
0         Non-trainable params
12        Total params
0.000     Total estimated model params size (MB)
c:\Users\alosius.ak

Training: |          | 0/? [00:00<?, ?it/s]

forget = 0.0
candidate = 0.0
input = 0.0
new_long = 0.0
output = 0.0
new short = 0.0


forget = 0.10396257042884827
candidate = -0.4230036735534668
input = 0.15395760536193848
new_long = 0.060459211468696594
output = 0.21295028924942017
new short = 0.033395517617464066


forget = 0.1937049776315689
candidate = -0.8477426171302795
input = 0.290434330701828
new_long = 0.11788226664066315
output = 0.41297227144241333
new short = 0.07061479240655899


forget = 0.38578176498413086
candidate = -1.6956839561462402
input = 0.5788671374320984
new_long = 0.15107238292694092
output = 0.8244642019271851
new short = 0.10423122346401215


forget = 0.4138503074645996
candidate = -1.6940147876739502
input = 0.6138304471969604
new_long = 0.08489270508289337
output = 0.8498011827468872
new short = 0.05932705104351044


forget = 0.18110373616218567
candidate = -0.8506494164466858
input = 0.2753011882305145
new_long = 0.12665578722953796
output = 0.40137413144111633
new short = 0.07546596974134445


forge

`Trainer.fit` stopped: `max_epochs=3000` reached.


forget = 0.993998110294342
candidate = 0.4898715615272522
input = -0.256319522857666
new_long = -0.15554600954055786
output = 0.5480732321739197
new short = -0.09778039902448654


forget = 1.1909763813018799
candidate = 0.11696505546569824
input = -0.1557597517967224
new_long = -0.20105978846549988
output = 0.8493637442588806
new short = -0.1389615684747696


forget = 1.425724983215332
candidate = -0.21195226907730103
input = 0.012425750494003296
new_long = -0.15654468536376953
output = 1.1639747619628906
new short = -0.11833050101995468


forget = 1.9639521837234497
candidate = -0.7897399067878723
input = 0.4718550443649292
new_long = 7.301568984985352e-07
output = 1.8174359798431396
new short = 6.281234163907357e-07


forget = 2.042917251586914
candidate = -0.6977729201316833
input = 0.6132383346557617
new_long = 0.18157298862934113
output = 1.8452847003936768
new short = 0.15510068833827972


forget = 1.6219606399536133
candidate = 0.01659432053565979
input = 0.3637763261795044
new_

In [ ]:
print("Company B: observed = 0.5, Predicted = ", model.forward(torch.tensor([1., 0.5, 0.25, 1.])).detach())

forget = 2.042917251586914
candidate = -0.6977729201316833
input = 0.6132383346557617
new_long = 0.18157298862934113
output = 1.8452847003936768
new short = 0.15510068833827972


forget = 1.6219606399536133
candidate = 0.01659432053565979
input = 0.3637763261795044
new_long = 0.32733920216560364
output = 1.2331814765930176
new short = 0.24480150640010834


forget = 1.4195905923843384
candidate = 0.3832213580608368
input = 0.25356292724609375
new_long = 0.4112285375595093
output = 0.9299894571304321
new short = 0.2793109714984894


forget = 2.22930908203125
candidate = -0.4806910753250122
input = 0.9469637870788574
new_long = 0.6534145474433899
output = 1.9110195636749268
new short = 0.499999463558197


Company B: observed = 0.5, Predicted =  tensor(0.5000)


In [ ]:
print(model.input_format(model.wlr1, model.wlr2, model.blr1))
print(model.input_format(model.wpr1, model.wpr2, model.bpr1))
print(model.input_format(model.wp1, model.wp2, model.bp1))
print(model.input_format(model.wo1, model.wo2, model.bo1))

{'input_weights': 1048, 'gate_biases': 993998, 'short_weights': 667}
{'input_weights': -1187, 'gate_biases': 489871, 'short_weights': 777}
{'input_weights': 869, 'gate_biases': -256319, 'short_weights': 1194}
{'input_weights': 1297, 'gate_biases': 548073, 'short_weights': 235}


In [ ]:
x = list([[5, 9], [5, 6]])
s = type(x)
if (s == list):
    if type(x[0]) == list:
        print("list")
    else:
        print("int")
else:
    print((s))

list


In [ ]:
def values(input):
        output_string = ''
        if (type(input) == int):
            output_string += str(input)
        elif type(input) == list:
            output_string = '('
            if type(input[0]) == int:
                for k, i in enumerate(input):
                    print(i)
                    output_string += str(i)
                    if k == len(input)-1:
                        break
                    output_string += ", "
                output_string += ')'

            elif type(input[0]) == list:
                for k, i in enumerate(input):
                    output_string += '('
                    for inner, j in enumerate(i):
                        output_string += str(j)
                        if inner == len(i)-1:
                            break
                        output_string += ", "
                    output_string += ')'
                    if k == len(input)-1:
                        break
                    output_string += ','
                output_string += ')'
        return output_string

In [ ]:
print(values([[2,3,4], [9,8,9]]))

((2, 3, 4),(9, 8, 9))


In [ ]:
a = 0.95 * 1 + 0.86
print(a)
b = 95 * 1 + 86
print(f"b = {b/10}")

1.81
b = 18.1


In [ ]:
tanh = [-761,-757,-753,-748,-744,-739,-735,-730,-725,-721,-716,-711,-706,-701,-696,-691,-685,-680,-675,-669,-664,-658,-652,-646,-641,-635,-629,-623,-616,-610,-604,-597,-591,-584,-578,-571,-564,-558,-551,-544,-537,-529,-522,-515,-507,-500,-492,-485,-477,-469,-462,-454,-446,-438,-430,-421,-413,-405,-396,-388,-379,-371,-362,-353,-345,-336,-327,-318,-309,-300,-291,-282,-272,-263,-254,-244,-235,-226,-216,-206,-197,-187,-178,-168,-158,-148,-139,-129,-119,-109,-99,-89,-79,-69,-59,-49,-39,-29,-19,-9,0,9,19,29,39,49,59,69,79,89,99,109,119,129,139,148,158,168,178,187,197,206,216,226,235,244,254,263,272,282,291,300,309,318,327,336,345,353,362,371,379,388,396,405,413,421,430,438,446,454,462,469,477,485,492,500,507,515,522,529,537,544,551,558,564,571,578,584,591,597,604,610,616,623,629,635,641,646,652,658,664,669,675,680,685,691,696,701,706,711,716,721,725,730,735,739,744,748,753,757,761,765,769,773,777,781,785,789,793,796,800,804,807,811,814,817,821,824,827,830,833,836,839,842,845,848,851,853,856,859,861,864,866,869,871,874,876,878,880,883,885,887,889,891,893,895,897,899,901,903,905,906,908,910,912,913,915,917,918,920,921,923,924,926,927,928,930,931,932,934,935,936,937,939,940,941,942,943,944,945,946,947,948,949,950,951,952,953,954,955,956,957,957,958,959,960,961,961,962,963,964,964,965,966,966,967,968,968,969,969,970,971,971,972,972,973,973,974,974,975,975,976,976,977,977,978,978,978,979,979,980,980,980,981,981,981,982,982,983,983,983,983,984,984,984,985,985,985,986,986,986,986,987,987,987,987,988,988,988,988,989,989,989,989,989,990,990,990,990,990,991,991,991,991,991,991,992,992,992,992,992,992,992,993,993,993,993,993,993,993,993,994,994,994,994,994,994,994,994,994,995,995,995,995,995,995,995,995,995,995,995,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999]
tanh[1100]
len(tanh)#

1101

In [ ]:
sig = [268,270,272,274,276,278,280,282,284,286,289,291,293,295,297,299,301,303,305,307,310,312,314,316,318,320,323,325,327,329,331,334,336,338,340,342,345,347,349,352,354,356,358,361,363,365,368,370,372,375,377,379,382,384,386,389,391,394,396,398,401,403,406,408,410,413,415,418,420,423,425,428,430,432,435,437,440,442,445,447,450,452,455,457,460,462,465,467,470,472,475,477,480,482,485,487,490,492,495,497,500,502,504,507,509,512,514,517,519,522,524,527,529,532,534,537,539,542,544,547,549,552,554,557,559,562,564,567,569,571,574,576,579,581,584,586,589,591,593,596,598,601,603,605,608,610,613,615,617,620,622,624,627,629,631,634,636,638,641,643,645,647,650,652,654,657,659,661,663,665,668,670,672,674,676,679,681,683,685,687,689,692,694,696,698,700,702,704,706,708,710,713,715,717,719,721,723,725,727,729,731,733,734,736,738,740,742,744,746,748,750,752,753,755,757,759,761,763,764,766,768,770,772,773,775,777,779,780,782,784,785,787,789,790,792,794,795,797,798,800,802,803,805,806,808,809,811,813,814,816,817,819,820,822,823,824,826,827,829,830,832,833,834,836,837,838,840,841,842,844,845,846,848,849,850,851,853,854,855,856,858,859,860,861,862,864,865,866,867,868,869,871,872,873,874,875,876,877,878,879,880,881,882,883,884,885,886,887,888,889,890,891,892,893,894,895,896,897,898,899,900,901,902,902,903,904,905,906,907,908,908,909,910,911,912,912,913,914,915,916,916,917,918,919,919,920,921,922,922,923,924,924,925,926,926,927,928,928,929,930,930,931,932,932,933,934,934,935,935,936,937,937,938,938,939,939,940,941,941,942,942,943,943,944,944,945,945,946,946,947,947,948,948,949,949,950,950,951,951,952,952,953,953,953,954,954,955,955,956,956,956,957,957,958,958,958,959,959,960,960,960,961,961,961,962,962,963,963,963,964,964,964,965,965,965,966,966,966,967,967,967,968,968,968,968,969,969,969,970,970,970,970,971,971,971,972,972,972,972,973,973,973,973,974,974,974,974,975,975,975,975,976,976,976,976,977,977,977,977,977,978,978,978,978,978,979,979,979,979,979,980,980,980,980,980,981,981,981,981,981,982,982,982,982,982,982,983,983,983,983,983,983,984,984,984,984,984,984,984,985,985,985,985,985,985,985,986,986,986,986,986,986,986,987,987,987,987,987,987,987,987,987,988,988,988,988,988,988,988,988,989,989,989,989,989,989,989,989,989,989,990,990,990,990,990,990,990,990,990,990,990,991,991,991,991,991,991,991,991,991,991,991,991,992,992,992,992,992,992,992,992,992,992,992,992,992,993,993,993,993,993,993,993,993,993,993,993,993,993,993,993,994,994,994,994,994,994,994,994,994,994,994,994,994,994,994,994,994,994,994,995,995,995,995,995,995,995,995,995,995,995,995,995,995,995,995,995,995,995,995,995,995,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,996,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,997,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,998,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999,999]
sig[151]

624

In [ ]:
def computation(nbits):
        compute_string = ''
        for i in range(nbits):
            if i == nbits-1:
                compute_string += f'(ints({nbits-i-1})*{2**i});'
                return compute_string
            compute_string += f'(ints({nbits-i-1})*{2**i}) + '

In [ ]:
print("num := "+computation(10))

num := (ints(9)*1) + (ints(8)*2) + (ints(7)*4) + (ints(6)*8) + (ints(5)*16) + (ints(4)*32) + (ints(3)*64) + (ints(2)*128) + (ints(1)*256) + (ints(0)*512);


In [6]:
def input_format(wsh, win, b, dp):
        if type(b) == float:
            data = {
                "input_weights": int(win*10**dp),
                "gate_biases":int(b*10**(dp*2)),
                "short_weights":int(wsh*10**dp)
            }
        else:
            data = {
                "input_weights": [int(x*10**dp) for x in win],
                "gate_biases":[int(x*10**(dp*2)) for x in b],
                "short_weights":[int(x*10**dp) for x in wsh]
            }
        return data

input_format(0.5, 10.0, 0.02, 3)

{'input_weights': 10000, 'gate_biases': 20000, 'short_weights': 500}